In [1]:
!pip install openpyxl
# !echo Artur119289 | sudo -S pip3 install --user --upgrade pandas
import requests
from bs4 import BeautifulSoup
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
import json
import os
import re
import urllib3
import urllib.parse
from urllib.request import urlopen
from urllib.parse import urlparse
import numpy as np
import pandas as pd
import progressbar
import time
from requests.auth import HTTPBasicAuth

Defaulting to user installation because normal site-packages is not writeable
DEPRECATION: python-debian 0.1.43ubuntu1 has a non-standard version number. pip 24.1 will enforce this behaviour change. A possible replacement is to upgrade to a newer version of python-debian or contact the author to suggest that they release a version with a conforming version number. Discussion can be found at https://github.com/pypa/pip/issues/12063


/tmp/ipykernel_37505/3575917780.py:15: DeprecationWarning: 
Pyarrow will become a required dependency of pandas in the next major release of pandas (pandas 3.0),
(to allow more performant data types, such as the Arrow string type, and better interoperability with other libraries)
but was not found to be installed on your system.
If this would cause problems for you,
please provide us feedback at https://github.com/pandas-dev/pandas/issues/54466
        
  import pandas as pd


In [2]:
companies = pd.read_excel('Companies.xlsx')

In [3]:
links = input().split()
links = list(set(links))

 https://www.ru.abbott/ https://www.alcoa.com/global/en/home/ https://novabev.com/ https://biocad.ru/ https://www.bp.com/ https://www.evraz.com/ru/ https://www.pwc.com/gx/en.html https://www.x5.ru/ru/ https://www.vtb.ru/ https://www.pik.ru/ https://alfabank.ru/ https://www.tinkoff.ru/ http://www.sberbank.ru/ru/person https://www.vtb.ru/ https://spbbank.ru/ https://business.rsb.ru/ https://www.gazprombank.ru/ https://www.raiffeisen.ru/ https://www.rosneft.ru/ https://lukoil.ru/ https://www.x5.ru/ru/ https://www.gazprom.ru/ https://www.gkm.ru/ https://www.tatneft.ru/ https://moskva.mts.ru/personal https://www.tplusgroup.ru/ https://www.evraz.com/ru/ https://www.eurochem.ru/ https://msk.tele2.ru/ https://www.novatek.ru/ https://sovcombank.ru/?utm_referrer=https%3A%2F%2Fwww.google.com%2F https://moscow.megafon.ru/ https://moskva.mts.ru/personal https://moskva.beeline.ru/customers/products/ https://uralsib.ru/ https://www.citibank.ru/russia/main/rus/home.htm https://www.cherkizovo.ru/ https

In [4]:
links

['https://www.tatneft.ru/',
 'https://moscow.megafon.ru/',
 'https://www.cherkizovo.ru/',
 'https://spbbank.ru/',
 'https://www.novatek.ru/',
 'https://www.sakhalinenergy.ru/ru/',
 'https://moskva.beeline.ru/customers/products/',
 'https://www.pik.ru/',
 'https://www.citibank.ru/russia/main/rus/home.htm',
 'https://www.evraz.com/ru/',
 'https://www.gazprom.ru/',
 'https://sovcombank.ru/?utm_referrer=https%3A%2F%2Fwww.google.com%2F',
 'https://biocad.ru/',
 'https://www.pwc.com/gx/en.html',
 'https://business.rsb.ru/',
 'https://www.raiffeisen.ru/',
 'https://www.ru.abbott/',
 'https://www.gkm.ru/',
 'https://uralsib.ru/',
 'https://alfabank.ru/',
 'https://www.vtb.ru/',
 'https://moskva.mts.ru/personal',
 'https://www.bp.com/',
 'https://www.alcoa.com/global/en/home/',
 'https://www.tplusgroup.ru/',
 'https://lukoil.ru/',
 'https://www.tinkoff.ru/',
 'https://www.gazprombank.ru/',
 'https://www.rosneft.ru/',
 'https://www.eurochem.ru/',
 'http://www.sberbank.ru/ru/person',
 'https://do

In [14]:
def get_status(logs):
    for log in logs:
        if log['message']:
            d = json.loads(log['message'])
            try:
                content_type = 'text/html' in d['message']['params']['response']['headers']['content-type']
                response_received = d['message']['method'] == 'Network.responseReceived'
                if content_type and response_received:
                    return d['message']['params']['response']['status']
            except:
                pass

def preprocess(line):
    return ' '.join(line.replace('\r',' ').replace('\xa0',' ').replace('\xad', ' ').strip().split())

def get_text(soup):
    text = []
    for script in soup(["script", "style","footer","input",'link','meta','button']):
        script.extract()

    paragraph = '\n'.join(list(dict.fromkeys([text for text in soup.stripped_strings])))
    return paragraph


def get_all_links(url,link_hierarchy,soup):
    child_links = []
    for script in soup(["script", "style"]):
        script.extract()
    
    sublinks = [a.get('href') for a in soup.find_all('a') if a.get('href') and a.get('href').startswith('/')]
    
    sublinks = [link[1:] for link in sublinks]
    sublinks = [*set(sublinks)]
    sublinks = list(filter(None, sublinks))
    
    for link in sublinks:
        if ".pdf" not in link or ".PDF" not in link:
            if 'www' in link:
                new_url = os.path.join(url[:url.rfind('www')], urlparse(url).netloc, link)
            else:
                new_url = os.path.join(url[:url.rfind('//')+2], urlparse(url).netloc, link)
            child_links.append(new_url)
    
    link_hierarchy[url] = child_links
    return

def get_responce(links):
    responses = []
    selenium = []
    status = 0
    page = ''
    header = {
  'accept':'text/html,application/xhtml+xml,application/xml;q=0.9,image/webp,image/apng,*/*;q=0.8,application/signed-exchange;v=b3',
  'accept-encoding':'gzip, deflate, br',
  'accept-language':'ru-RU,ru;q=0.9,en-US;q=0.8,en;q=0.7',
  'cache-control':'no-cache',
  'dnt': '1',
  'pragma': 'no-cache',
  'sec-fetch-mode': 'navigate',
  'sec-fetch-site': 'none',
  'sec-fetch-user': '?1',
  'upgrade-insecure-requests': '1',
  'user-agent': 'Mozilla/5.0 (Windows NT 6.1; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/76.0.3809.100 Safari/537.36'
    }
    for link in links:
        try:
            page = requests.get(link,verify=False)
            status = page.status_code
        except:
            page = requests.get(link)
            status = page.status_code
        if status == 401:    
            page = requests.get(link,headers=header,auth=HTTPBasicAuth('user', 'pass'),verify=False)
            status = page.status_code
            print(link, status, sep=' : ')
        if status == 200:
            page.encoding = 'utf-8'
            responses.append((link, page.text))
            print(link, status, sep=' : ')
        
        else:
            page.encoding = 'utf-8'
            selenium.append(link)
            print(link, status, sep=' : ')
        status = 0

In [6]:
chrome_options = webdriver.ChromeOptions()
chrome_options.add_argument('--headless')
chrome_options.add_argument('--no-sandbox')
chrome_options.add_argument('--disable-dev-shm-usage')
chrome_options.add_argument('--disable-blink-features=AutomationControlled')
chrome_options.set_capability('goog:loggingPrefs', {'performance': 'ALL'})
driver = webdriver.Chrome(options = chrome_options)

In [15]:
get_responce(links)

/usr/lib/python3/dist-packages/urllib3/connectionpool.py:1015: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.tatneft.ru'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
  warnings.warn(
/usr/lib/python3/dist-packages/urllib3/connectionpool.py:1015: InsecureRequestWarning: Unverified HTTPS request is being made to host 'moscow.megafon.ru'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
  warnings.warn(


https://www.tatneft.ru/ : 403
https://moscow.megafon.ru/ : 200


/usr/lib/python3/dist-packages/urllib3/connectionpool.py:1015: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.cherkizovo.ru'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
  warnings.warn(


https://www.cherkizovo.ru/ : 200
https://spbbank.ru/ : 200


/usr/lib/python3/dist-packages/urllib3/connectionpool.py:1015: InsecureRequestWarning: Unverified HTTPS request is being made to host 'spbbank.ru'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
  warnings.warn(
/usr/lib/python3/dist-packages/urllib3/connectionpool.py:1015: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.novatek.ru'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
  warnings.warn(


...

/usr/lib/python3/dist-packages/urllib3/connectionpool.py:1015: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.raiffeisen.ru'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
  warnings.warn(


https://www.raiffeisen.ru/ : 200


/usr/lib/python3/dist-packages/urllib3/connectionpool.py:1015: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.ru.abbott'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
  warnings.warn(


https://www.ru.abbott/ : 200


SSLError: HTTPSConnectionPool(host='www.gkm.ru', port=443): Max retries exceeded with url: / (Caused by SSLError(SSLError(1, '[SSL: DH_KEY_TOO_SMALL] dh key too small (_ssl.c:1007)')))

In [25]:
page = requests.get('https://www.vtb.ru/', auth=HTTPBasicAuth('user', 'pass'))
status = page.status_code
status

403

In [6]:
responses

[('https://www.el5-energo.ru/',
  '<html lang="ru">\r\n<head>\r\n    <title>ЭЛ5-Энерго</title>\r\n    <meta name="viewport" content="width=device-width, initial-scale=1">\r\n    <meta name="google-site-verification" content="search">\r\n    <link rel="icon" type="image/vnd.microsoft.icon" href="/bitrix/templates/enel_v2/img/favicon.ico">\r\n    <link rel="shortcut icon" type="image/vnd.microsoft.icon" href="/bitrix/templates/enel_v2/img/favicon.ico">\r\n\r\n<meta http-equiv="Content-Type" content="text/html; charset=UTF-8" />\n<meta name="robots" content="index, follow" />\n<meta name="keywords" content="ЭЛ5-Энерго" />\n<meta name="description" content="ЭЛ5-Энерго" />\n<link href="/bitrix/templates/enel_v2/css/aos.css?166835893226053" type="text/css"  rel="stylesheet" />\n<link href="/bitrix/templates/enel_v2/components/bitrix/news.list/index.banners/style.css?1662483880162" type="text/css"  rel="stylesheet" />\n<link href="/bitrix/templates/enel_v2/components/bitrix/news.list/press.re

In [7]:
for link in selenium:
    driver.get(link)
    logs = driver.get_log('performance')
    print(link,' : ',get_status(logs))

https://samolet.ru  :  401


In [8]:
link_hierarchy = {}
for i in range(len(responses)):
    soup = BeautifulSoup(responses[i][1],'html.parser')
    get_all_links(responses[i][0],link_hierarchy,soup)

In [9]:
link_hierarchy

{'https://www.el5-energo.ru/': ['https://www.el5-energo.ru/upload/iblock/752/7r4yvyl33bnwq4evi4085i42ppop07jt/The_Azov_Wind_Power_Plant_project_of_EL5_Energo_received_the_status_of_a_climate_project.pdf',
  'https://www.el5-energo.ru/about-us/electricity-generation/',
  'https://www.el5-energo.ru/services/connection-to-heating-systems/',
  'https://www.el5-energo.ru/suppliers/document-and-contacts/',
  'https://www.el5-energo.ru/media/stories/2023/power_engineers_day/',
  'https://www.el5-energo.ru/upload/iblock/ea1/vgzjyn8t5ddngglos1gdmq44ynyqti2p/The_first_agreements_on_selling_the_green_certificates_of_Azov_and_Kola_Wind_Farms_under_the_national_certification_system_are_signed.pdf',
  'https://www.el5-energo.ru/investors/',
  'https://www.el5-energo.ru/services/',
  'https://www.el5-energo.ru/services/sale-of-non-core-assets/',
  'https://www.el5-energo.ru/media/stories/2024/winners_2023/',
  'https://www.el5-energo.ru/about-us/management-team/',
  'https://www.el5-energo.ru/supplie

In [28]:
test_data = pd.DataFrame(columns=['Parent Link', 'Actual Link', 'Page Text'])
for i in range(len(responses)):
    linklist = link_hierarchy[responses[i][0]]
    parent = responses[i][0]
    for link in linklist:
       try:
            current_response = requests.get(link)
            soup = BeautifulSoup(current_response.text,'html.parser')
            if ('.pdf' in link) or ('.doc' in link):
                row = {'Parent Link': [parent], 'Actual Link': [link], 'Page Text': ['File']}
            else:
                row = {'Parent Link': [parent], 'Actual Link': [link], 'Page Text': [get_text(soup)]}
            test_data = pd.concat([test_data,pd.DataFrame(row)],ignore_index = True)
            print('one link done\n')
       except:
            pass
    print('----------------\n next link\n--------------------------')

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

one link done

----------------
 next link
--------------------------
one link done

one link done

one link done

one link done

one link done

one link done



In [29]:
test_data['Page Text'].unique()

array(['File',
       'Как работают электростанции ПАО «ЭЛ5‑Энерго»\nПАО «ЭЛ5-Энерго»\nО нас\nАктивы\nГРЭС и ВЭС\nРуководство\nНаши лидеры\nКарьера\nВозможности и развитие\nГенерация электроэнергии\nКак работают электростанции\nМедиа\nПресс-релизы\nНовости\nИстории\nИнвесторам\nУстойчивое развитие\nУслуги\nЗеленая энергия\nПодключение к системам теплоснабжения\nПродажа непрофильных активов\nПоставщикам\nДокументы и контакты\nКвалификация поставщиков\nПлан закупок\nПокупка мазута\nEN\nQuick links\nInformation disclosure\nPress releases\nBasic documents\nПервый мобильный телефон весил около килограмма, а разряжался буквально за полчаса разговора. Современные смартфоны очень легкие, могут держать зарядку несколько дней и часто намного мощнее, чем компьютеры. Но и те, и другие не могли бы работать без электричества.\nЧтобы вскипятить воду на огне нужно 10-15 минут, а электрический чайник нагреет ее за 2-3 минуты. При этом сам выключится и не потребует к себе лишнего внимания.\nВ среднем на

In [30]:
test_data.to_csv('Test.csv',escapechar=' ',encoding='utf-8-sig')

In [31]:
test_data.iloc[202]['Actual Link']

'https://www.russneft.ru/shareholders/information_disclosure/issuing_documents/'